In [6]:
import pandas as pd
import spacy
from spacy.matcher import PhraseMatcher
from spacy.tokens import Span
import random

In [39]:
#Import 
df = pd.read_excel('../data/combined-training-final.xlsx')

In [40]:
df.head()

Body
0  This app looks awesome.  Very well thought out design and it appears that most of the functions are right at my fingertips.  Not so.  I have used it mostly for categorizing expenses.  I was trying to run a report, but nothing really made sense.  I went first to google to look for some tutorial videos, but it appears that most of the videos available online are only advertisements.  That is when I went to the help and support section in app.  In the section there is a FAQs area.  Perfect!  When I read the only article in this section I thought it must be some kind of joke.  It was an article on how to get to the FAQs section on the app.  It is like some perverted Groundhog Day scene, or like when you are reviewing a resume for a potential new hire and one of the sections is the filler text from the template they created the resume from.  I expect more from this company.  Fix this or simply remove it.
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             This update is terrible basically unusable please change it back ASAP
2                                                                                                                                                                                                                                                                                                                                                                              The majority of the time this app is wonderful. On a regular basis it will completely close out and I will lose the transaction I’m in the middle of. \nI’ve continually notified Intuit about this since the problem started in April of 2019. The consistent response is that they close out the ticket same day and never respond or research the issue. \nToday I’m told that they no longer have a department to help customers with the app. \nNow I’ve just recently renewed my annual subscription so I’m out that money because this product is unreliable.
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                One my favorite apps to use while working. I’m on it like a social media page. Thanks quick books.
4                                                                                                                                                                                                                                                                                                                                          

In [41]:
#DF styles..

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_colwidth', None)

th_props = [
  ('font-size', '11px'),
  ('text-align', 'center'),
  ('font-weight', 'bold'),
  ('color', '#6d6d6d'),
  ('background-color', '#f7f7f9')
  ]

# Set CSS properties for td elements in dataframe
td_props = [
  ('font-size', '11px'),
  ('text-align', 'left')
  ]

# Set table styles
styles = [
  dict(selector="th", props=th_props),
  dict(selector="td", props=td_props)
  ]


(df.style
    .set_table_styles(styles))

In [42]:
nlp = spacy.load('en_core_web_sm')

df.review = df.Body.str.lower()

print(nlp.pipe_names)

['tagger', 'parser', 'ner']


/Users/eelrufaie/Library/Python/3.7/lib/python/site-packages/ipykernel_launcher.py:3: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  This is separate from the ipykernel package so we can avoid doing imports until


In [ ]:
class EntityMatcher(object):
    name = "entity_matcher"

    def __init__(self, nlp, terms, label):
        patterns = [nlp.make_doc(text) for text in terms]
        self.matcher = PhraseMatcher(nlp.vocab)
        self.matcher.add(label, None, *patterns)

    def __call__(self, doc):
        matches = self.matcher(doc)
        for match_id, start, end in matches:
            span = Span(doc, start, end, label=match_id)
            doc.ents = list(doc.ents) + [span]
        return doc

In [ ]:
aspect_terms = []
for review in nlp.pipe(df.Body):
    chunks = [(chunk.root.text) for chunk in review.noun_chunks if chunk.root.pos_ == 'NOUN']
    aspect_terms.append(', '.join(chunks))
df['aspect_terms'] = aspect_terms

In [ ]:
df.sample(25)

In [4]:
import json

filename = "../data/train_ner.json"
print(filename)


with open(filename) as train_data:
	train = json.load(train_data)

TRAIN_DATA_NEW = []
for data in train:
	ents = [tuple(entity) for entity in data['entities']]
	TRAIN_DATA_NEW.append((data['content'],{'entities':ents}))


with open('{}'.format(filename.replace('json','txt')),'w') as write:
	write.write(str(TRAIN_DATA_NEW))

print('-------------Copy and Paste to spacy training-------------')
print()
print()
print()
# print(TRAIN_DATA_NEW)
print()
print()
print()
print('--------------------------End-----------------------------')

../data/train_ner.json
-------------Copy and Paste to spacy training-------------






--------------------------End-----------------------------


In [7]:

def train_spacy(data,iterations):
    TRAIN_DATA = data
    nlp = spacy.blank('en')  # create blank Language class
    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if 'ner' not in nlp.pipe_names:
        ner = nlp.create_pipe('ner')
        nlp.add_pipe(ner, last=True)
       

    # add labels
    for _, annotations in TRAIN_DATA:
         for ent in annotations.get('entities'):
            ner.add_label(ent[2])

    # get names of other pipes to disable them during training
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
    with nlp.disable_pipes(*other_pipes):  # only train NER
        optimizer = nlp.begin_training()
        for itn in range(iterations):
            print("Statring iteration " + str(itn))
            random.shuffle(TRAIN_DATA)
            losses = {}
            for text, annotations in TRAIN_DATA:
#                 print('---')
#                 print('text:' + text)
#                 print(annotations)
                nlp.update(
                    [text],  # batch of texts
                    [annotations],  # batch of annotations
                    drop=0.2,  # dropout - make it harder to memorise data
                    sgd=optimizer,  # callable to update weights
                    losses=losses)
            print(losses)
    return nlp


prdnlp = train_spacy(TRAIN_DATA_NEW, 20)

Statring iteration 0
{'ner': 882.685852520622}
Statring iteration 1
{'ner': 458.3969667188678}
Statring iteration 2
{'ner': 359.2912551546349}
Statring iteration 3
{'ner': 332.1649724656092}
Statring iteration 4
{'ner': 270.95001494869643}
Statring iteration 5
{'ner': 227.51994460382622}
Statring iteration 6
{'ner': 184.18267689551305}
Statring iteration 7
{'ner': 141.2670921990605}
Statring iteration 8
{'ner': 160.44511661445057}
Statring iteration 9
{'ner': 174.5750615769363}
Statring iteration 10
{'ner': 130.9754826045678}
Statring iteration 11
{'ner': 135.09076390943753}
Statring iteration 12
{'ner': 111.33204204574298}
Statring iteration 13
{'ner': 176.55219752628594}
Statring iteration 14
{'ner': 138.64888209660822}
Statring iteration 15
{'ner': 97.62781945217961}
Statring iteration 16
{'ner': 101.28022304123697}
Statring iteration 17
{'ner': 98.56724670390211}
Statring iteration 18
{'ner': 79.72137708234567}
Statring iteration 19
{'ner': 106.55351981226346}


In [8]:
# Save our trained Model
prdnlp.to_disk("qbo_aspect")

In [9]:
#Test your text
test_text = ["Cancelling your subscription seems impossible. I've emailed, called, used their help menu. It shouldn't be this hard. Still trying to cancel.",
              "My App has stopped working on my Samsung s9 for 2 days in a row. You should have sent an email to inform subscribers if your app is going to be experiencing a downtime.",
              "Cannot open customer invoices. Please correct ASAP!",
               "bugs on iOS13 please update ASAP!"]
for text in test_text:
    print('-----')
    doc = prdnlp(text)
    for ent in doc.ents:
        print('keyword=' + ent.text, 'aspect=' + ent.label_)

-----
keyword=subscription aspect=Subscription
-----
keyword=App aspect=App
-----
keyword=invoices aspect=Estimates
-----
keyword=bugs aspect=Quality


In [43]:
for index, row in df.iterrows():
    aspect_terms = []
    doc = prdnlp(row['Body'])
    for ent in doc.ents:
        if ent.label_ not in aspect_terms:
            aspect_terms.append(ent.label_)

    df.loc[index,'aspect_terms'] = ", ".join(aspect_terms)

In [44]:
df.style.set_table_styles(
    [{"selector": "td", "props": [("text-align", "left")]}]
).set_precision(2)

In [45]:
df.to_csv('../data/auto_trained.csv', index = False)

In [13]:
df.sample(25)

Rating                                    Aspects  \
21        3                                    General   
219       1                 general,quality,experience   
169       1                                     Update   
151       1                               Subscription   
403       1               updates,quality,subscription   
141       1                 General, Customers Service   
134       5                                    General   
234       1      compatibility,mileage,experience,help   
394       1              updates,experience,navigation   
343       1                       update,quality,price   
111       2                           Quality, Banking   
382       5                         general,experience   
337       4                             update,quality   
85        1                                    Quality   
157       5                                    Updates   
162       2                                    Quality   
0         1                 Customers Service, Quality   
187       1                                  Dashboard   
184       1                                    General   
242       1                              general,price   
33        2                                Attachments   
61        2                                    General   
72        5                                 Experience   
98        5                                  Estimates   
352       2  customers service,data,experience,updates   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           Body  \
21                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Blessed and grtfl   
219                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  app stinks   
169                                                                                                                                                                                                                                                                                                                                                                                    